In [0]:
import cv2

In [0]:
import mahotas

ModuleNotFoundError: ignored

In [0]:
!pip install mahotas

     |████████████████████████████████| 1.5MB 2.8MB/s 
  Created wheel for mahotas: filename=mahotas-1.4.9-cp36-cp36m-linux_x86_64.whl size=4264029 sha256=0702b77026bf98a0389fc682de17663f2f3c59d08b44b8e451de0e81c862974e
  Stored in directory: /root/.cache/pip/wheels/02/e7/50/b67eee3b19c479cc5b41f10230bf9c1556be6eaaf095c6e997
Successfully built mahotas


In [0]:
import mahotas

In [48]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [0]:
import pandas as pd

In [0]:
data = pd.read_csv("/content/drive/My Drive/paintings-emotion-classifier-master/data/cgm.csv") 

In [0]:
data

Unnamed: 0  ...                                              color
0             0  ...  [7.2743428e-01 1.5668061e-01 1.5365528e-02 3.2...
1             1  ...  [8.8726006e-02 1.5525027e-01 4.0190045e-02 1.5...
2             2  ...  [0.08724698 0.21892232 0.42528883 0.05945243 0...
3             3  ...  [0.1692699  0.11249724 0.12987842 0.2336414  0...
4             4  ...  [3.6494511e-01 1.7879070e-01 8.5517131e-02 3.1...
..          ...  ...                                                ...
133         133  ...  [2.3389153e-01 5.9889182e-02 3.2372531e-03 9.9...
134         134  ...  [4.4911009e-01 2.5566688e-01 5.4734547e-02 6.6...
135         135  ...  [1.5225086e-01 2.2333723e-01 3.5084280e-01 2.4...
136         136  ...  [6.5485555e-01 4.4688795e-02 5.6560226e-03 5.8...
137         137  ...  [8.7629147e-02 9.2683181e-02 1.7860173e-01 1.8...

[138 rows x 5 columns]

In [0]:
data['shape']

0      [6.12165496e-01 8.53641074e-07 8.42887980e-09 ...
1      [3.05940838e-01 3.52945331e-06 3.22176814e-10 ...
2      [2.88194473e-01 9.93158674e-07 1.08345695e-09 ...
3      [3.39368867e-01 1.94352462e-06 1.32849103e-08 ...
4      [3.55454021e-01 2.63307771e-06 6.22479383e-09 ...
                             ...                        
133    [6.24447136e-01 4.58053640e-05 4.07079489e-08 ...
134    [5.01436059e-01 5.48178620e-06 8.28425119e-09 ...
135    [3.25762261e-01 1.16283426e-06 6.07426437e-10 ...
136    [8.73448567e-01 1.79960120e-05 2.07744517e-08 ...
137    [3.23856861e-01 3.51149947e-07 3.45655660e-09 ...
Name: shape, Length: 138, dtype: object

In [0]:
data['shape'][0]

'[6.12165496e-01 8.53641074e-07 8.42887980e-09 3.04261605e-08\n 2.70965924e-11 2.88240071e-11 2.70965914e-11]'

In [0]:
type(data['shape'][0])

str

In [0]:
float('3.04261605e-08\n')

3.04261605e-08

In [0]:
import os

In [0]:
name = []
shape = []
texture = []
color = []
final_data = {'name':[],'expression':"anger",'train/test':"test",'shape':[],'texture':[],'color':[]}
def fd_hu_moments(image):
    image = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    feature = cv2.HuMoments(cv2.moments(image)).flatten()
    return feature

def fd_haralick(image):
    # convert the image to grayscale
    gray = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    # compute the haralick texture feature vector
    haralick = mahotas.features.haralick(gray).mean(axis=0)
    # return the result
    return haralick

def fd_histogram(image, mask=None):
    # convert the image to HSV color-space
    image = cv2.cvtColor(image, cv2.COLOR_BGR2HSV)
    # compute the color histogram
    hist  = cv2.calcHist([image], [0, 1, 2], None, [3, 3, 3], [0, 256, 0, 256, 0, 256])
    # normalize the histogram
    cv2.normalize(hist, hist)
    # return the histogram
    return hist.flatten()

#image = cv2.imread("708 copy.jpeg")
#print(image)
#print(len(fd_histogram(image)))
directory = "/content/drive/My Drive/paintings-emotion-classifier-master/data/anger/crop/test/"
for filename in os.listdir(directory):
  if filename.endswith(".jpeg"):
    s = directory+filename
    image = cv2.imread(s)
    print(image)
    name.append(filename)
    shape.append(fd_hu_moments(image))
    texture.append(fd_haralick(image))
    color.append(fd_histogram(image))
#print(data)


def change_arr(arr):
	minimum = None
	maximum = None
	for j in range(len(arr[0])):
		for i in range(len(arr)):
			if minimum==None and maximum==None:
				minimum = arr[i][j]
				maximum = arr[i][j]
			else:
				minimum = min(minimum,arr[i][j])
				maximum = max(maximum,arr[i][j])
	for j in range(len(arr[0])):
		for i in range(len(arr)):
			arr[i][j] = (arr[i][j]-minimum)/(maximum-minimum)
	return arr

shape = change_arr(shape)
texture = change_arr(texture)
color = change_arr(color)

final_data['name'] = name
final_data['shape'] = shape
final_data['texture'] = texture
final_data['color'] = color

df = pd.DataFrame(final_data)
df.to_csv(r'/content/drive/My Drive/paintings-emotion-classifier-master/data/main.csv',mode='a')

[[[30 49 54]
  [30 49 54]
  [32 48 54]
  ...
  [33 52 60]
  [33 52 60]
  [34 53 61]]

 [[30 49 54]
  [30 49 54]
  [32 48 54]
  ...
  [32 51 59]
  [33 52 60]
  [33 52 60]]

 [[30 49 54]
  [30 49 54]
  [30 49 54]
  ...
  [32 51 59]
  [33 52 60]
  [33 52 60]]

 ...

 [[22 19 21]
  [21 20 22]
  [32 31 33]
  ...
  [33 52 65]
  [34 53 66]
  [34 53 66]]

 [[33 28 29]
  [30 28 28]
  [30 28 28]
  ...
  [32 51 64]
  [31 50 63]
  [31 50 63]]

 [[32 28 27]
  [32 28 27]
  [33 28 29]
  ...
  [32 51 64]
  [31 50 63]
  [31 50 63]]]
[[[  0   7  57]
  [  0   7  57]
  [  0   7  62]
  ...
  [ 42  54 120]
  [ 43  57 123]
  [ 44  58 124]]

 [[  0   8  61]
  [  0   7  62]
  [  2   9  66]
  ...
  [ 42  56 122]
  [ 45  59 125]
  [ 46  61 124]]

 [[  0   3  62]
  [  2   6  65]
  [  2   7  68]
  ...
  [ 41  58 121]
  [ 43  60 123]
  [ 44  62 123]]

 ...

 [[156 155 157]
  [176 175 177]
  [170 169 171]
  ...
  [ 81  90 154]
  [ 83  92 156]
  [ 84  93 157]]

 [[186 185 187]
  [200 199 201]
  [190 189 191]
  ...
  

In [0]:
picture_data = pd.read_csv("/content/drive/My Drive/paintings-emotion-classifier-master/data/cgm.csv")
painting_data = pd.read_csv("/content/drive/My Drive/paintings-emotion-classifier-master/data/main.csv")

In [0]:
final_data = {'name':[],'expression':"anger",'train/test':"test",'shape':[],'texture':[],'color':[]}

In [52]:
picture_data

Unnamed: 0  ...                                              color
0             0  ...  [7.2743428e-01 1.5668061e-01 1.5365528e-02 3.2...
1             1  ...  [8.8726006e-02 1.5525027e-01 4.0190045e-02 1.5...
2             2  ...  [0.08724698 0.21892232 0.42528883 0.05945243 0...
3             3  ...  [0.1692699  0.11249724 0.12987842 0.2336414  0...
4             4  ...  [3.6494511e-01 1.7879070e-01 8.5517131e-02 3.1...
..          ...  ...                                                ...
133         133  ...  [2.3389153e-01 5.9889182e-02 3.2372531e-03 9.9...
134         134  ...  [4.4911009e-01 2.5566688e-01 5.4734547e-02 6.6...
135         135  ...  [1.5225086e-01 2.2333723e-01 3.5084280e-01 2.4...
136         136  ...  [6.5485555e-01 4.4688795e-02 5.6560226e-03 5.8...
137         137  ...  [8.7629147e-02 9.2683181e-02 1.7860173e-01 1.8...

[138 rows x 5 columns]

In [53]:
painting_data

Unnamed: 0  ...                                              color
0            0.0  ...  [8.6044021e-02 1.4540696e-01 1.7243519e-01 7.3...
1            1.0  ...  [0.38745412 0.7821829  0.36373243 0.16826579 0...
2            2.0  ...  [3.0000821e-02 2.7288571e-02 6.0389109e-02 3.5...
3            3.0  ...  [8.0357209e-02 9.7576603e-02 6.7376959e-01 1.4...
4            4.0  ...  [1.3207379e-01 4.3754172e-02 6.6204554e-01 7.1...
...          ...  ...                                                ...
4743       133.0  ...  [1.0170962e-01 3.0937633e-01 9.0195537e-01 1.6...
4744       134.0  ...  [3.2025713e-01 1.2524429e-01 4.3629584e-01 1.7...
4745       135.0  ...  [8.8516960e-04 0.0000000e+00 1.2645280e-04 2.9...
4746       136.0  ...  [0.94585484 0.2978923  0.18023211 0.         0...
4747       137.0  ...  [0.2891226  0.08436728 0.2934791  0.39622867 0...

[4748 rows x 7 columns]

In [54]:
print(len(painting_data))
print(len(picture_data))

4748
138


In [0]:
from math import sqrt

In [56]:
picture_data['shape'][0]

'[6.12165496e-01 8.53641074e-07 8.42887980e-09 3.04261605e-08\n 2.70965924e-11 2.88240071e-11 2.70965914e-11]'

In [0]:
def eculedian(paint_shape,x_shape):
  sum = 0
  if paint_shape==None or x_shape==None:
    return 10000
  for i in range(min(len(paint_shape),len(x_shape))):
    sum+=(paint_shape[i]-x_shape[i])**2
  return sqrt(sum)

In [0]:
def get_shape(picture_data,paint):
  shape = []
  paint_shape = paint.split(" ")
  paint_shape[0] = paint_shape[0].replace("[","")
  paint_shape[-1] = paint_shape[-1].replace("]","")
  x_paint_shape = []
  for i in paint_shape:
    if i:
      try:
        x_paint_shape.append(float(i))
      except:
        continue
    else:
      x_paint_shape.append(float(0))
  paint_shape = x_paint_shape
  minimum = None
  minimum1 = None
  min_point = None
  min1_point = None
  for i in range(len(picture_data)):
    x_shape = picture_data['shape'][i]
    x_shape = x_shape.split(" ")
    x_shape[0] = x_shape[0].replace("[","")
    x_shape[-1] = x_shape[-1].replace("]","")
    #print(x_shape)
    new_x_shape = []
    for j in x_shape:
      if j:
        try:
          new_x_shape.append(float(j))
        except:
          continue
      else:
        new_x_shape.append(float(0))
    #x_shape = list(map(float,x_shape))
    #print(x_shape)
    k = eculedian(paint_shape,new_x_shape)
    if minimum==None:
      minimum = k
      min_point = new_x_shape
    elif k>minimum and minimum1==None:
      minimum1 = k
      min1_point = new_x_shape
    elif k<=minimum:
      minimum = k
      min_point = new_x_shape
    elif k>minimum and k<=minimum:
      minimum1 = k
      min1_point = new_x_shape
    #shape.append()
  return minimum/eculedian(min1_point,min_point)

In [0]:
def get_texture(picture_data,paint):
  shape = []
  paint_shape = paint.split(" ")
  paint_shape[0] = paint_shape[0].replace("[","")
  paint_shape[-1] = paint_shape[-1].replace("]","")
  x_paint_shape = []
  for i in paint_shape:
    if i:
      try:
        x_paint_shape.append(float(i))
      except:
        continue
    else:
      x_paint_shape.append(float(0))
  paint_shape = x_paint_shape
  minimum = None
  minimum1 = None
  min_point = None
  min1_point = None
  for i in range(len(picture_data)):
    x_shape = picture_data['texture'][i]
    x_shape = x_shape.split(" ")
    x_shape[0] = x_shape[0].replace("[","")
    x_shape[-1] = x_shape[-1].replace("]","")
    #print(x_shape)
    #print(x_shape)
    new_x_shape = []
    for j in x_shape:
      if j!="":
        try:
          new_x_shape.append(float(j))
        except:
          continue
      else:
        new_x_shape.append(float(0))
    #x_shape = list(map(float,x_shape))
    #print(x_shape)
    k = eculedian(paint_shape,new_x_shape)
    if minimum==None:
      minimum = k
      min_point = new_x_shape
    elif k>minimum and minimum1==None:
      minimum1 = k
      min1_point = new_x_shape
    elif k<=minimum:
      minimum = k
      min_point = new_x_shape
    elif k>minimum and k<=minimum:
      minimum1 = k
      min1_point = new_x_shape
    #shape.append()
  return minimum/eculedian(min1_point,min_point)

In [0]:
def get_color(picture_data,paint):
  shape = []
  paint_shape = paint.split(" ")
  paint_shape[0] = paint_shape[0].replace("[","")
  paint_shape[-1] = paint_shape[-1].replace("]","")
  #paint_shape = list(map(float,paint_shape))
  x_paint_shape = []
  for i in paint_shape:
    if i:
      try:
        x_paint_shape.append(float(i))
      except:
        continue
    else:
      x_paint_shape.append(float(0))
  paint_shape = x_paint_shape
  minimum = None
  minimum1 = None
  min_point = None
  min1_point = None
  for i in range(len(picture_data)):
    x_shape = picture_data['color'][i]
    x_shape = x_shape.split(" ")
    x_shape[0] = x_shape[0].replace("[","")
    x_shape[-1] = x_shape[-1].replace("]","")
    #print(x_shape)
    new_x_shape = []
    for j in x_shape:
      if j:
        try:
          new_x_shape.append(float(j))
        except:
          continue
      else:
        new_x_shape.append(float(0))
    #x_shape = list(map(float,x_shape))
    #print(x_shape)
    k = eculedian(paint_shape,new_x_shape)
    if minimum==None:
      minimum = k
      min_point = new_x_shape
    elif k>minimum and minimum1==None:
      minimum1 = k
      min1_point = new_x_shape
    elif k<=minimum:
      minimum = k
      min_point = new_x_shape
    elif k>minimum and k<=minimum:
      minimum1 = k
      min1_point = new_x_shape
    #shape.append()
  return minimum/eculedian(min1_point,min_point)

In [0]:
def get_result(arr):
  a = [0]*len(arr)
  return a

In [163]:
for i in range(len(painting_data)):
  final_data = {'name':"",'expression':"",'train/test':"",'shape':[],'texture':[],'color':[]}
  final_data['name'] = painting_data['name'][i]
  final_data['expression'] = painting_data['expression'][i]
  final_data['train/test'] = painting_data['train/test'][i]
  #print(painting_data['shape'][i])
  k = get_shape(picture_data,painting_data['shape'][i])
  if k>=1:
    final_data['shape'].append(painting_data['shape'][i])
  else:
    final_data['shape'].append(get_result(painting_data['shape'][i]))
  k = get_texture(picture_data,painting_data['texture'][i])
  if k>=1:
    final_data['texture'].append(painting_data['texture'][i])
  else:
    final_data['texture'].append(get_result(painting_data['texture'][i]))
  k = get_color(picture_data,painting_data['color'][i])
  if k>=1:
    final_data['color'].append(painting_data['color'][i])
  else:
    final_data['color'].append(get_result(painting_data['color'][i]))
  print(final_data)
  df = pd.DataFrame(final_data)
  df.to_csv(r'/content/drive/My Drive/paintings-emotion-classifier-master/data/main_cgm.csv',mode='a')
  #print(final_data)
  


{'name': '016 copy.jpeg', 'expression': 'sad', 'train/test': 'train', 'shape': ['[2.13447129e-01 7.01436811e-08 5.34630925e-09 7.17084985e-10\n 8.18422949e-11 8.18527742e-11 8.18422949e-11]'], 'texture': [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]], 'color': [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0